In [49]:
import io
import pandas as pd
import requests
import numpy as np
import h3
from os import listdir

# check for the vbohcar.xlsx file in the current directory
if 'VBOHCAR.xlsx' in listdir():
        # read the third sheet of the excel file
    vb_ohca_in = pd.read_excel('VBOHCAR.xlsx', sheet_name=3)
else:
    # clone the excel file from github
    url = 'https://github.com/INFORMSJoC/2020.1022/blob/master/results/VBOHCAR.xlsx?raw=true'
    file = requests.get(url)
    file_bytes = io.BytesIO(file.content)
    # read the third sheet of the excel file
    vb_ohca_in = pd.read_excel(file_bytes, sheet_name=3)
vb_ohca_in.head()

ID_OHCA        ReceivedTime  MinimumResponseTime   Latitude  Longitude  \
0        1 2017-01-01 00:49:54             5.666667  36.862471 -76.024169   
1        2 2017-01-01 06:35:29            20.750000  36.766897 -76.042337   
2        3 2017-01-01 06:56:25             9.650000  36.766897 -76.042337   
3        4 2017-01-01 17:05:56            11.083333  36.905880 -76.118769   
4        5 2017-01-01 19:53:20             0.000000  36.620850 -76.090090   

            Incident_Location       X_OHCA       Y_OHCA       Z_OHCA  
0     1000 LINDSLEY DR_x000D_  1232.449963 -4951.984772  3826.080166  
1  2600 SPRINGHAVEN DR_x000D_  1232.417401 -4958.562301  3817.562796  
2  2600 SPRINGHAVEN DR_x000D_  1232.417401 -4958.562301  3817.562796  
3        4200 SHORE DR_x000D_  1223.576354 -4951.197334  3829.945177  
4   5200 BLACKWATER RD_x000D_  1230.619605 -4969.017372  3804.526862

In [50]:
def hexid_ohca(df: pd.DataFrame, lat_col: str, lon_col: str, res: int = 9) -> pd.DataFrame:
    """
    This function takes a dataframe of OHCA incidents and returns a dictionary
    with the hex_id as the key and the count
    of OHCA incidents as the value.
    :param df: a dataframe of OHCA incidents
    :param lat_col: the name of the column with the latitude values
    :param lon_col: the name of the column with the longitude values
    :param res: the resolution of the hex_id
    :return: a dictionary with the hex_id as the key and the count of OHCA incidents as the value
    """
    # create a dictionary to hold the hex_id and the count of OHCA incidents
    hexid_ohca_cnt = {}
    for _, row in df.iterrows():
        # get the hex_id for each row
        hex_id = h3.latlng_to_cell(np.float64(row[lat_col]), np.float64(row[lon_col]), res)
        # if the hex_id is not in the dictionary, add it
        if hex_id not in hexid_ohca_cnt:
            hexid_ohca_cnt[hex_id] = 0
        # increment the count of OHCA in the hex_id
        hexid_ohca_cnt[hex_id] += 1
    
    return hexid_ohca_cnt


hexid_ohca_cnt = hexid_ohca(vb_ohca_in, 'Latitude', 'Longitude', 9)

# create a dataframe from the dictionary with the hex_id as the index
main_ohca_df = pd.DataFrame.from_dict(hexid_ohca_cnt, orient='index', columns=['OHCA'])
print(sum(main_ohca_df['OHCA']))
main_ohca_df.head()

2706


OHCA
892af636e43ffff     3
892af0c96abffff     2
892af63720bffff     4
892af051523ffff     2
892af6266bbffff     2

In [51]:
mtgmry_ohca_df = pd.read_csv('montgomery/mtgmry_unfiltered.csv')
# filter by 'title' containing 'CARDIAC ARREST'
mtgmry_ohca_df = mtgmry_ohca_df[mtgmry_ohca_df['title'].str.contains('CARDIAC ARREST')]
# timeStamp contatins 2017 2018 2019
mtgmry_ohca_df = mtgmry_ohca_df[mtgmry_ohca_df['timeStamp'].str.contains('2017|2018|2019')]
# create a dictionary to hold the counts of OHCA in each hex_id
hexid_ohca_cnt = {}
# iterate through the rows of the dataframe
for i, row in mtgmry_ohca_df.iterrows():
    # get the hex_id for each row
    hex_id = h3.latlng_to_cell(np.float64(row['lat']), np.float64(row['lng']), 9)
    # if the hex_id is not in the dictionary, add it
    if hex_id not in hexid_ohca_cnt:
        hexid_ohca_cnt[hex_id] = 0
    # increment the count of OHCA in the hex_id
    hexid_ohca_cnt[hex_id] += 1

mtgmry_ohca_df = pd.DataFrame.from_dict(hexid_ohca_cnt, orient='index', columns=['OHCA'])
print(sum(mtgmry_ohca_df['OHCA']))
# add the OHCA count to the main dataframe
main_ohca_df = pd.concat([main_ohca_df, mtgmry_ohca_df], ignore_index=False, axis=0)
main_ohca_df.head()

4773


OHCA
892af636e43ffff     3
892af0c96abffff     2
892af63720bffff     4
892af051523ffff     2
892af6266bbffff     2

In [52]:
# read cinncinati data
cinncinati_ohca_df = pd.read_csv('cincinnati/Cincinnati_Fire_Incidents__CAD___including_EMS__ALS_BLS_.csv')
# remove rows with NaN values in 'LATITUDE_X' or 'LONGITUDE_X'
cinncinati_ohca_df.dropna(subset=['LATITUDE_X', 'LONGITUDE_X'], inplace=True)
# filter by 'INCIDENT_TYPE_DESC' containing 'CARDIAC' and STROKE (CVA) / CFD_INCIDENT_TYPE_GROUP containing 'CARDIAC'
# first fill the NaN values with empty strings
cinncinati_ohca_df['INCIDENT_TYPE_DESC'].fillna('', inplace=True)
cinncinati_ohca_df['CFD_INCIDENT_TYPE_GROUP'].fillna('', inplace=True)
cinncinati_ohca_df = cinncinati_ohca_df[cinncinati_ohca_df['CFD_INCIDENT_TYPE_GROUP'].str.contains('CARDIAC')]
# filter CREATE_TIME_INCIDENT containing 2017 2018 2019
cinncinati_ohca_df = cinncinati_ohca_df[cinncinati_ohca_df['CREATE_TIME_INCIDENT'].str.contains('2017|2018|2019')]

# create a dictionary to hold the counts of OHCA in each hex_id
hexid_ohca_cin = hexid_ohca(cinncinati_ohca_df, 'LATITUDE_X', 'LONGITUDE_X', 9)
# create a dataframe from the dictionary with the hex_id as the index
cinncinati_ohca_df = pd.DataFrame.from_dict(hexid_ohca_cin, orient='index', columns=['OHCA'])
print(sum(cinncinati_ohca_df['OHCA']))
# add the OHCA count to the main dataframe
main_ohca_df = pd.concat([main_ohca_df, cinncinati_ohca_df], ignore_index=False, axis=0)

1453


In [53]:
# now read virginia_beach data
main_hexagon_df = pd.read_csv('virginia_beach_osm.csv')
main_hexagon_df.rename(columns={'Unnamed: 0': 'hex_id'}, inplace=True)
# pivot the dataframe to have the hex_id as the index
main_hexagon_df.set_index('hex_id', inplace=True)
main_hexagon_df.head()

animal_boarding  atm  bank_x  bar_x  bbq  bench  \
hex_id                                                             
892af0500a7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af05019bffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0501b3ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0504c7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af050527ffff              0.0  0.0     0.0    0.0  0.0    0.0   

                 bicycle_parking  bicycle_rental  bicycle_repair_station  \
hex_id                                                                     
892af0500a7ffff              0.0             0.0                     0.0   
892af05019bffff              0.0             0.0                     0.0   
892af0501b3ffff              0.0             0.0                     0.0   
892af0504c7ffff              0.0             0.0                     0.0   
892af050527ffff              0.0             0.0                     0.0   

                 cafe_x  ...  storage_tank_neighbour_count  \
hex_id                   ...                                 
892af0500a7ffff     0.0  ...                             0   
892af05019bffff     0.0  ...                             0   
892af0501b3ffff     0.0  ...                             0   
892af0504c7ffff     0.0  ...                             0   
892af050527ffff     0.0  ...                             0   

                 studio_neighbour_count  terrace_neighbour_count  \
hex_id                                                             
892af0500a7ffff                       0                        0   
892af05019bffff                       0                        0   
892af0501b3ffff                       0                        0   
892af0504c7ffff                       0                        0   
892af050527ffff                       0                        0   

                 theatre_y_neighbour_count  toilets_y_neighbour_count  \
hex_id                                                                  
892af0500a7ffff                          0                          0   
892af05019bffff                          0                          0   
892af0501b3ffff                          0                          0   
892af0504c7ffff                          0                          0   
892af050527ffff                          0                          0   

                 townhall_neighbour_count  university_y_neighbour_count  \
hex_id                                                                    
892af0500a7ffff                         0                             0   
892af05019bffff                         0                             0   
892af0501b3ffff                         0                             0   
892af0504c7ffff                         0                             0   
892af050527ffff                         0                             0   

                 veterinary_y_neighbour_count  warehouse_neighbour_count  \
hex_id                                                                     
892af0500a7ffff                             0                          0   
892af05019bffff                             0                          0   
892af0501b3ffff                             0                          0   
892af0504c7ffff                             0                          0   
892af050527ffff                             0                          0   

                 yes_neighbour_count  
hex_id                                
892af0500a7ffff                    0  
892af05019bffff                    0  
892af0501b3ffff                    0  
892af0504c7ffff                    0  
892af050527ffff                    0  

[5 rows x 308 columns]

In [54]:
# add montgomery
mtgmry_hexagon_df = pd.read_csv('montgomery_osm.csv')
mtgmry_hexagon_df.rename(columns={'Unnamed: 0': 'hex_id'}, inplace=True)
# pivot the dataframe to have the hex_id as the index
mtgmry_hexagon_df.set_index('hex_id', inplace=True)
main_hexagon_df = pd.concat([main_hexagon_df, mtgmry_hexagon_df], ignore_index=False, axis=0)
main_hexagon_df.head()

animal_boarding  atm  bank_x  bar_x  bbq  bench  \
hex_id                                                             
892af0500a7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af05019bffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0501b3ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0504c7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af050527ffff              0.0  0.0     0.0    0.0  0.0    0.0   

                 bicycle_parking  bicycle_rental  bicycle_repair_station  \
hex_id                                                                     
892af0500a7ffff              0.0             0.0                     0.0   
892af05019bffff              0.0             0.0                     0.0   
892af0501b3ffff              0.0             0.0                     0.0   
892af0504c7ffff              0.0             0.0                     0.0   
892af050527ffff              0.0             0.0                     0.0   

                 cafe_x  ...  lighthouse_neighbour_count  no_neighbour_count  \
hex_id                   ...                                                   
892af0500a7ffff     0.0  ...                         NaN                 NaN   
892af05019bffff     0.0  ...                         NaN                 NaN   
892af0501b3ffff     0.0  ...                         NaN                 NaN   
892af0504c7ffff     0.0  ...                         NaN                 NaN   
892af050527ffff     0.0  ...                         NaN                 NaN   

                 recycling_y_neighbour_count  shopping_center_neighbour_count  \
hex_id                                                                          
892af0500a7ffff                          NaN                              NaN   
892af05019bffff                          NaN                              NaN   
892af0501b3ffff                          NaN                              NaN   
892af0504c7ffff                          NaN                              NaN   
892af050527ffff                          NaN                              NaN   

                 social_facility_y_neighbour_count  stable_neighbour_count  \
hex_id                                                                       
892af0500a7ffff                                NaN                     NaN   
892af05019bffff                                NaN                     NaN   
892af0501b3ffff                                NaN                     NaN   
892af0504c7ffff                                NaN                     NaN   
892af050527ffff                                NaN                     NaN   

                 synagogue_neighbour_count  temple_neighbour_count  \
hex_id                                                               
892af0500a7ffff                        NaN                     NaN   
892af05019bffff                        NaN                     NaN   
892af0501b3ffff                        NaN                     NaN   
892af0504c7ffff                        NaN                     NaN   
892af050527ffff                        NaN                     NaN   

                 tower_neighbour_count  university_neighbour_count  
hex_id                                                              
892af0500a7ffff                    NaN                         NaN  
892af05019bffff                    NaN                         NaN  
892af0501b3ffff                    NaN                         NaN  
892af0504c7ffff                    NaN                         NaN  
892af050527ffff                    NaN                         NaN  

[5 rows x 390 columns]

In [55]:
# add the OHCA count to the main dataframe
main_hexagon_df = pd.concat([main_hexagon_df, main_ohca_df], ignore_index=False, axis=1)
# save to a csv file
main_hexagon_df.head()

animal_boarding  atm  bank_x  bar_x  bbq  bench  \
892af0500a7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af05019bffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0501b3ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0504c7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af050527ffff              0.0  0.0     0.0    0.0  0.0    0.0   

                 bicycle_parking  bicycle_rental  bicycle_repair_station  \
892af0500a7ffff              0.0             0.0                     0.0   
892af05019bffff              0.0             0.0                     0.0   
892af0501b3ffff              0.0             0.0                     0.0   
892af0504c7ffff              0.0             0.0                     0.0   
892af050527ffff              0.0             0.0                     0.0   

                 cafe_x  ...  no_neighbour_count  recycling_y_neighbour_count  \
892af0500a7ffff     0.0  ...                 NaN                          NaN   
892af05019bffff     0.0  ...                 NaN                          NaN   
892af0501b3ffff     0.0  ...                 NaN                          NaN   
892af0504c7ffff     0.0  ...                 NaN                          NaN   
892af050527ffff     0.0  ...                 NaN                          NaN   

                 shopping_center_neighbour_count  \
892af0500a7ffff                              NaN   
892af05019bffff                              NaN   
892af0501b3ffff                              NaN   
892af0504c7ffff                              NaN   
892af050527ffff                              NaN   

                 social_facility_y_neighbour_count  stable_neighbour_count  \
892af0500a7ffff                                NaN                     NaN   
892af05019bffff                                NaN                     NaN   
892af0501b3ffff                                NaN                     NaN   
892af0504c7ffff                                NaN                     NaN   
892af050527ffff                                NaN                     NaN   

                 synagogue_neighbour_count  temple_neighbour_count  \
892af0500a7ffff                        NaN                     NaN   
892af05019bffff                        NaN                     NaN   
892af0501b3ffff                        NaN                     NaN   
892af0504c7ffff                        NaN                     NaN   
892af050527ffff                        NaN                     NaN   

                 tower_neighbour_count  university_neighbour_count  OHCA  
892af0500a7ffff                    NaN                         NaN   NaN  
892af05019bffff                    NaN                         NaN   NaN  
892af0501b3ffff                    NaN                         NaN   NaN  
892af0504c7ffff                    NaN                         NaN   NaN  
892af050527ffff                    NaN                         NaN   NaN  

[5 rows x 391 columns]

In [56]:
# add cinncinati
cinncinati_hexagon_df = pd.read_csv('cincinnati_osm.csv')
cinncinati_hexagon_df.rename(columns={'Unnamed: 0': 'hex_id'}, inplace=True)
# pivot the dataframe to have the hex_id as the index
cinncinati_hexagon_df.set_index('hex_id', inplace=True)
main_hexagon_df = pd.concat([main_hexagon_df, cinncinati_hexagon_df], ignore_index=False, axis=0)
# fill the NaN values with 0
main_hexagon_df.fillna(0, inplace=True)
main_hexagon_df.to_csv('main_hexagon_df.csv')
main_hexagon_df.head()

animal_boarding  atm  bank_x  bar_x  bbq  bench  \
892af0500a7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af05019bffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0501b3ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af0504c7ffff              0.0  0.0     0.0    0.0  0.0    0.0   
892af050527ffff              0.0  0.0     0.0    0.0  0.0    0.0   

                 bicycle_parking  bicycle_rental  bicycle_repair_station  \
892af0500a7ffff              0.0             0.0                     0.0   
892af05019bffff              0.0             0.0                     0.0   
892af0501b3ffff              0.0             0.0                     0.0   
892af0504c7ffff              0.0             0.0                     0.0   
892af050527ffff              0.0             0.0                     0.0   

                 cafe_x  ...  nightclub_neighbour_count  \
892af0500a7ffff     0.0  ...                        0.0   
892af05019bffff     0.0  ...                        0.0   
892af0501b3ffff     0.0  ...                        0.0   
892af0504c7ffff     0.0  ...                        0.0   
892af050527ffff     0.0  ...                        0.0   

                 nursing_home_neighbour_count  porch_neighbour_count  \
892af0500a7ffff                           0.0                    0.0   
892af05019bffff                           0.0                    0.0   
892af0501b3ffff                           0.0                    0.0   
892af0504c7ffff                           0.0                    0.0   
892af050527ffff                           0.0                    0.0   

                 religious_neighbour_count  \
892af0500a7ffff                        0.0   
892af05019bffff                        0.0   
892af0501b3ffff                        0.0   
892af0504c7ffff                        0.0   
892af050527ffff                        0.0   

                 semidetached_house_neighbour_count  \
892af0500a7ffff                                 0.0   
892af05019bffff                                 0.0   
892af0501b3ffff                                 0.0   
892af0504c7ffff                                 0.0   
892af050527ffff                                 0.0   

                 social_centre_y_neighbour_count  studio_y_neighbour_count  \
892af0500a7ffff                              0.0                       0.0   
892af05019bffff                              0.0                       0.0   
892af0501b3ffff                              0.0                       0.0   
892af0504c7ffff                              0.0                       0.0   
892af050527ffff                              0.0                       0.0   

                 tank_neighbour_count  train_station_neighbour_count  \
892af0500a7ffff                   0.0                            0.0   
892af05019bffff                   0.0                            0.0   
892af0501b3ffff                   0.0                            0.0   
892af0504c7ffff                   0.0                            0.0   
892af050527ffff                   0.0                            0.0   

                 tree_house_neighbour_count  
892af0500a7ffff                         0.0  
892af05019bffff                         0.0  
892af0501b3ffff                         0.0  
892af0504c7ffff                         0.0  
892af050527ffff                         0.0  

[5 rows x 511 columns]

In [57]:
# read the csv file
poland_df = pd.read_csv('warszawa_osm.csv')
# set unnamed column name to hex_id
poland_df.rename(columns={'Unnamed: 0': 'hex_id'}, inplace=True)
# pivot the dataframe to have the hex_id as the index
poland_df.set_index('hex_id', inplace=True)
# delete columns not in training data
main_cols = list(main_hexagon_df.columns)
poland_cols = list(poland_df.columns)
for col in poland_cols:
    if col not in main_cols:
        del poland_df[col]
# fill the NaN values with 0
poland_df.head()

animal_boarding  animal_shelter  arts_centre_x  atm  bank_x  \
hex_id                                                                         
891f52240b3ffff              0.0             0.0            0.0  0.0     0.0   
891f52240b7ffff              0.0             0.0            0.0  0.0     0.0   
891f52244a7ffff              0.0             0.0            0.0  0.0     0.0   
891f5224513ffff              0.0             0.0            0.0  0.0     0.0   
891f522451bffff              0.0             0.0            0.0  0.0     0.0   

                 bar_x  bbq  bench  bicycle_rental  bicycle_repair_station  \
hex_id                                                                       
891f52240b3ffff    0.0  0.0    0.0             0.0                     0.0   
891f52240b7ffff    0.0  0.0    0.0             0.0                     0.0   
891f52244a7ffff    0.0  0.0    0.0             0.0                     0.0   
891f5224513ffff    0.0  0.0    2.0             0.0                     1.0   
891f522451bffff    0.0  0.0    0.0             0.0                     0.0   

                 ...  storage_tank_neighbour_count  studio_y_neighbour_count  \
hex_id           ...                                                           
891f52240b3ffff  ...                             0                         0   
891f52240b7ffff  ...                             0                         0   
891f52244a7ffff  ...                             0                         0   
891f5224513ffff  ...                             0                         0   
891f522451bffff  ...                             0                         0   

                 synagogue_neighbour_count  theatre_y_neighbour_count  \
hex_id                                                                  
891f52240b3ffff                          0                          0   
891f52240b7ffff                          0                          0   
891f52244a7ffff                          0                          0   
891f5224513ffff                          0                          0   
891f522451bffff                          0                          0   

                 toilets_y_neighbour_count  tower_neighbour_count  \
hex_id                                                              
891f52240b3ffff                          0                      0   
891f52240b7ffff                          0                      0   
891f52244a7ffff                          0                      0   
891f5224513ffff                          0                      0   
891f522451bffff                          0                      0   

                 train_station_neighbour_count  university_y_neighbour_count  \
hex_id                                                                         
891f52240b3ffff                              0                             0   
891f52240b7ffff                              0                             0   
891f52244a7ffff                              0                             0   
891f5224513ffff                              0                             0   
891f522451bffff                              0                             0   

                 veterinary_y_neighbour_count  yes_neighbour_count  
hex_id                                                              
891f52240b3ffff                             0                    0  
891f52240b7ffff                             0                    0  
891f52244a7ffff                             0                    0  
891f5224513ffff                             0                    0  
891f522451bffff                             0                    0  

[5 rows x 328 columns]

In [58]:
# drop columns in main_hexagon_df that are not in poland_df
main_cols = list(main_hexagon_df.columns)
poland_cols = list(poland_df.columns)
for col in main_cols:
    if col not in poland_cols and col != 'OHCA':
        del main_hexagon_df[col]

In [59]:
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

# shuffle the rows of the dataframe
main_hexagon_df = main_hexagon_df.sample(frac=1)

# create a dataframe with the OHCA count and the features
X = main_hexagon_df.drop(['OHCA'], axis=1)
y = main_hexagon_df['OHCA']
# split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)
# create the model
model = XGBRegressor(max_depth=1, n_jobs=-1)
# fit the model
model.fit(X_train, y_train)
# make predictions
y_pred = model.predict(X_test)
# calculate the mean squared error
mse = mean_squared_error(y_test, y_pred, squared=False)
print('MSE: %.2f' % mse)

MSE: 2.40


In [60]:
import h2o
from h2o.automl import H2OAutoML

# Start and connect to a local H2O cluster
h2o.init()
h2o_df = h2o.H2OFrame(main_hexagon_df)
x = list(main_hexagon_df.columns)  # Features
y = "OHCA"   # Target column
train, valid = h2o_df.split_frame(ratios=[0.8], seed=1234)
aml = H2OAutoML(max_runtime_secs=60, seed=1)  # You can adjust the parameters
aml.train(x=x, y=y, training_frame=train, validation_frame=valid)
lb = aml.leaderboard
print(lb)
best_model = aml.leader
predictions = best_model.predict(valid)
model_path = h2o.save_model(model=best_model, path="h2o_model_mojo", force=True)

Checking whether there is an H2O instance running at http://localhost:54321. connected.


--------------------------  ---------------------------------
H2O_cluster_uptime:         6 mins 17 secs
H2O_cluster_timezone:       Europe/Warsaw
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.44.0.3
H2O_cluster_version_age:    17 days
H2O_cluster_name:           H2O_from_python_radekaadek_y8w4bl
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    1.770 Gb
H2O_cluster_total_cores:    16
H2O_cluster_allowed_cores:  16
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.11.2 final
--------------------------  ---------------------------------

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |
21:35:14.682: _train param, Dropping bad and constant columns: [pub_x_neighbour_count, shelter_y_neighbour_count, community_centre_x_neighbour_count, residential_neighbour_count, dojo_x_neighbour_count, boathouse, events_venue_y, parcel_locker_neighbour_count, nightclub_y_neighbour_count, motorcycle_parking_neighbour_count, carport_neighbour_count, kindergarten_y_neighbour_count, post_box_neighbour_count, loading_dock_neighbour_count, cafe_y, bunker, clinic_x_neighbour_count, animal_shelter_neighbour_count, synagogue, police_x_neighbour_count, chapel, childcare_x_neighbour_count, fountain_y, theatre_y_neighbour_count, nursing_home_neighbour_count, pharmacy_x_neighbour_count, shed_neighbour_count, social_facility_y, grandstand, static_caravan, boathouse_neighbour_count, shower, religious, parking_space_neighbour_count, clinic_y, collapsed, cabin, civic, porch_neighbour_count

In [61]:

# read the csv file
poland_df = pd.read_csv('warszawa_osm.csv')
# set unnamed column name to hex_id
poland_df.rename(columns={'Unnamed: 0': 'hex_id'}, inplace=True)
# pivot the dataframe to have the hex_id as the index
poland_df.set_index('hex_id', inplace=True)
# delete columns not in training data
main_cols = list(main_hexagon_df.columns)
poland_cols = list(poland_df.columns)
for col in poland_cols:
    if col not in main_cols:
        del poland_df[col]
# sort by hex_id
poland_df.sort_index(inplace=True)
poland_df.head()

FileNotFoundError: [Errno 2] No such file or directory: 'warszawa_osm.csv'

In [ ]:
# make predictions
predictions = best_model.predict(h2o.H2OFrame(poland_df))
# convert the predictions to a pandas dataframe
predictions_df = predictions.as_data_frame()
# convert the predictions to a list
predictions_list = predictions_df['predict'].tolist()
# add the predictions to the dataframe
poland_df['OHCA'] = predictions_list

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
stackedensemble prediction progress: |███████████████████████████████████████████| (done) 100%


/home/radekaadek/myaed/.venv/lib/python3.11/site-packages/h2o/frame.py:1979: H2ODependencyWarning: converting H2O frame to pandas dataframe using single-thread.  For faster conversion using multi-thread, install datatable (for Python 3.9 or lower), or polars and pyarrow (for Python 3.10 or above).
  warnings.warn("converting H2O frame to pandas dataframe using single-thread.  For faster conversion using"
/tmp/ipykernel_2929/720802521.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  poland_df['OHCA'] = predictions_list


In [ ]:
# draw the map
import requests
aed_url = 'https://aed.openstreetmap.org.pl/aed_poland.geojson'
aed_file = requests.get(aed_url)
aed_json = aed_file.json()
# create a column with aed count
poland_df['aed_count'] = 0

# iterate through aeds find the hexagon and add 1 to the column
for aed in aed_json['features']:
    x, y = aed["geometry"]["coordinates"]
    hexagon = h3.latlng_to_cell(y, x, 9)
    if hexagon in poland_df.index:
        poland_df.loc[hexagon, 'aed_count'] += 1
# create a map, color hexagons by the predicted number of ohca
import folium

m = folium.Map(location=[52.2297, 21.0122], zoom_start=11)

max_ohca = poland_df['OHCA'].max()

# get top 10 hexagons with the most predicted ohca that have no defibrillators or hospitals
top_10_hexagons = poland_df[poland_df['aed_count'] == 0].sort_values(by='OHCA', ascending=False).head(10)

# add hexagons with opacity based on the number of ohca
for i, row in poland_df.iterrows():
    if row['aed_count'] == 0 and row['hospital_x'] == 0:
        boundary = h3.cell_to_boundary(i)
        if row['OHCA'] >= top_10_hexagons['OHCA'].min():
            folium.Polygon(locations=boundary, fill_color='blue', fill_opacity=row['OHCA']/max_ohca).add_to(m)
        else:
            folium.Polygon(locations=boundary, fill_color='red', fill_opacity=row['OHCA']/max_ohca).add_to(m)

    else:
        boundary = h3.cell_to_boundary(i)
        folium.Polygon(locations=boundary, fill_color='green', fill_opacity=row['OHCA']/max_ohca).add_to(m)
m.save('warsaw.html')
m

/tmp/ipykernel_2929/2274833285.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  poland_df['aed_count'] = 0
